# Collaboration and Competition

---

In this notebook, you will learn how to use the Unity ML-Agents environment for the third project of the [Deep Reinforcement Learning Nanodegree](https://www.udacity.com/course/deep-reinforcement-learning-nanodegree--nd893) program.

### 1. Start the Environment

We begin by importing the necessary packages.  If the code cell below returns an error, please revisit the project instructions to double-check that you have installed [Unity ML-Agents](https://github.com/Unity-Technologies/ml-agents/blob/master/docs/Installation.md) and [NumPy](http://www.numpy.org/).

In [1]:
from unityagents import UnityEnvironment
import numpy as np

from datetime import datetime
def MSG(txt):
    print('\n',datetime.now().strftime("%Y-%m-%d %H:%M:%S:"), str(txt))

Next, we will start the environment!  **_Before running the code cell below_**, change the `file_name` parameter to match the location of the Unity environment that you downloaded.

- **Mac**: `"path/to/Tennis.app"`
- **Windows** (x86): `"path/to/Tennis_Windows_x86/Tennis.exe"`
- **Windows** (x86_64): `"path/to/Tennis_Windows_x86_64/Tennis.exe"`
- **Linux** (x86): `"path/to/Tennis_Linux/Tennis.x86"`
- **Linux** (x86_64): `"path/to/Tennis_Linux/Tennis.x86_64"`
- **Linux** (x86, headless): `"path/to/Tennis_Linux_NoVis/Tennis.x86"`
- **Linux** (x86_64, headless): `"path/to/Tennis_Linux_NoVis/Tennis.x86_64"`

For instance, if you are using a Mac, then you downloaded `Tennis.app`.  If this file is in the same folder as the notebook, then the line below should appear as follows:
```
env = UnityEnvironment(file_name="Tennis.app")
```

In [2]:
env = UnityEnvironment(file_name="./Tennis_Windows_x86_64/Tennis.exe")

INFO:unityagents:
'Academy' started successfully!
Unity Academy name: Academy
        Number of Brains: 1
        Number of External Brains : 1
        Lesson number : 0
        Reset Parameters :
		
Unity brain name: TennisBrain
        Number of Visual Observations (per agent): 0
        Vector Observation space type: continuous
        Vector Observation space size (per agent): 8
        Number of stacked Vector Observation: 3
        Vector Action space type: continuous
        Vector Action space size (per agent): 2
        Vector Action descriptions: , 


Environments contain **_brains_** which are responsible for deciding the actions of their associated agents. Here we check for the first brain available, and set it as the default brain we will be controlling from Python.

In [3]:
# get the default brain
brain_name = env.brain_names[0]
brain = env.brains[brain_name]

### 2. Examine the State and Action Spaces

In this environment, two agents control rackets to bounce a ball over a net. If an agent hits the ball over the net, it receives a reward of +0.1.  If an agent lets a ball hit the ground or hits the ball out of bounds, it receives a reward of -0.01.  Thus, the goal of each agent is to keep the ball in play.

The observation space consists of 8 variables corresponding to the position and velocity of the ball and racket. Two continuous actions are available, corresponding to movement toward (or away from) the net, and jumping. 

Run the code cell below to print some information about the environment.

In [ ]:
# reset the environment
env_info = env.reset(train_mode=True)[brain_name]

# number of agents 
num_agents = len(env_info.agents)
print('Number of agents:', num_agents)

# size of each action
action_size = brain.vector_action_space_size
print('Size of each action:', action_size)

# examine the state space 
states = env_info.vector_observations
state_size = states.shape[1]
print('There are {} agents. Each observes a state with length: {}'.format(states.shape[0], state_size))
print('The state for the first agent looks like:', states[0])

Number of agents: 2
Size of each action: 2
There are 2 agents. Each observes a state with length: 24
The state for the first agent looks like: [ 0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.          0.          0.
  0.          0.          0.          0.         -6.65278625 -1.5
 -0.          0.          6.83172083  6.         -0.          0.        ]


### 3. Take Random Actions in the Environment

In the next code cell, you will learn how to use the Python API to control the agents and receive feedback from the environment.

Once this cell is executed, you will watch the agents' performance, if they select actions at random with each time step.  A window should pop up that allows you to observe the agents.

Of course, as part of the project, you'll have to change the code so that the agents are able to use their experiences to gradually choose better actions when interacting with the environment!

In [ ]:
for i in range(1, 6):                                      # play game for 5 episodes
    env_info = env.reset(train_mode=False)[brain_name]     # reset the environment    
    states = env_info.vector_observations                  # get the current state (for each agent)
    scores = np.zeros(num_agents)                          # initialize the score (for each agent)
    while True:
        actions = np.random.randn(num_agents, action_size) # select an action (for each agent)
        actions = np.clip(actions, -1, 1)                  # all actions between -1 and 1
        env_info = env.step(actions)[brain_name]           # send all actions to tne environment
        next_states = env_info.vector_observations         # get next state (for each agent)
        rewards = env_info.rewards                         # get reward (for each agent)
        dones = env_info.local_done                        # see if episode finished
        scores += env_info.rewards                         # update the score (for each agent)
        states = next_states                               # roll over states to next time step
        if np.any(dones):                                  # exit loop if episode finished
            break
    print('Score (max over agents) from episode {}: {}'.format(i, np.max(scores)))

Score (max over agents) from episode 1: 0.0
Score (max over agents) from episode 2: 0.09000000171363354
Score (max over agents) from episode 3: 0.0
Score (max over agents) from episode 4: 0.0
Score (max over agents) from episode 5: 0.0


When finished, you can close the environment.

In [ ]:
#env.close()

### 4. It's Your Turn!

Now it's your turn to train your own agent to solve the environment!  When training the environment, set `train_mode=True`, so that the line for resetting the environment looks like the following:
```python
env_info = env.reset(train_mode=True)[brain_name]
```

In [ ]:
import random
import torch
from collections import deque
import matplotlib.pyplot as plt
%matplotlib inline

from maddpg_agent_cpy import MADDPG

from workspace_utils import active_session

#agent = Agent(state_size=state_size, action_size=action_size, random_seed=10)
agent = MADDPG()

def maddpg(n_episodes=5000, max_t=10000, print_every=100):
    scores_deque = deque(maxlen=print_every)
    scores = []
    solved = 0
    t = 0
    MSG('start!')
    for i_episode in range(1, n_episodes+1):
        env_info = env.reset(train_mode=True)[brain_name]
        states = env_info.vector_observations
        #agent.reset()
        score = np.zeros(num_agents)
        #for t in range(max_t):
        #t = 0
        while True:
            if np.mean(scores_deque) <= 0.02:
                actions = agent.act(states,add_noise=True)
            else:
                actions = agent.act(states,add_noise=False)
            env_info = env.step(actions)[brain_name]           # send all actions to tne environment
            next_states = env_info.vector_observations         # get next state (for each agent)
            rewards = env_info.rewards                         # get reward (for each agent)
            dones = env_info.local_done                        # see if episode finished
            agent.step(states, actions, rewards, next_states, dones, t)
            score += rewards                                   # update the score (for each agent)
            states = next_states                               # roll over states to next time step
            t += 1
            if np.any(dones):                                  # exit loop if episode finished
                break
        scores_deque.append(np.mean(score))
        scores.append(np.mean(score))
        print('\rEpisode {}\tAverage Score: {:.4f}'.format(i_episode, np.mean(scores_deque)), end="")
        agent.save_weights()
        #torch.save(agent.actor_local.state_dict(), 'checkpoint_actor.pth')
        #torch.save(agent.critic_local.state_dict(), 'checkpoint_critic.pth')
        if i_episode % print_every == 0:
            print('\rEpisode {}\tAverage Score: {:.4f}'.format(i_episode, np.mean(scores_deque)))
            
        if np.mean(scores_deque)>=0.5 and solved!=1:
            print('\nEnvironment solved in {:d} episodes!\tAverage Score: {:.2f}'.format(i_episode, np.mean(scores_deque)))
            solved = 1
            #break
            
        if np.mean(scores_deque)>=0.75 and solved==1:
            print('\nAverage score of 0.75 or more achieved in {:d} episodes!\tAverage Score: {:.2f}'.format(i_episode, np.mean(scores_deque)))
            MSG('end!')
            break
            
    return scores

# with active_session():
    # do long-running work here
scores = maddpg()

fig = plt.figure()
ax = fig.add_subplot(111)
plt.plot(np.arange(1, len(scores)+1), scores)
plt.ylabel('Score')
plt.xlabel('Episode #')
plt.show()


 2018-12-11 08:48:14: start!
Stop adding noise

Stop adding noise

1
Stop adding noise

Stop adding noise

2
Stop adding noise

Stop adding noise

3
Stop adding noise

Stop adding noise

4
Stop adding noise

Stop adding noise

5
Stop adding noise

Stop adding noise

6
Stop adding noise

Stop adding noise

7
Stop adding noise

Stop adding noise

8

C:\Users\Win10\Anaconda3\envs\drlnd\lib\site-packages\numpy\core\fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\Users\Win10\Anaconda3\envs\drlnd\lib\site-packages\numpy\core\_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
C:\Users\Win10\Anaconda3\envs\drlnd\lib\site-packages\torch\nn\functional.py:995: UserWarning: nn.functional.tanh is deprecated. Use torch.tanh instead.
  warnings.warn("nn.functional.tanh is deprecated. Use torch.tanh instead.")



Stop adding noise

Stop adding noise

9
Stop adding noise

Stop adding noise

10
Stop adding noise

Stop adding noise

11
Stop adding noise

Stop adding noise

12
Stop adding noise

Stop adding noise

13
Stop adding noise

Stop adding noise

14
Episode 1	Average Score: -0.005015
16
17
18
19
20
21
22
23
24
25
26
27
28
Episode 2	Average Score: -0.005029
30
31
32
33
34
35
36
37
38
39
40
41
42
43
Episode 3	Average Score: -0.005044
45
46
47
48
49
50
51
52
53
54
55
56
57
Episode 4	Average Score: -0.005058
59
60
61
62
63
64
65
66
67
68
69
70
71
Episode 5	Average Score: -0.005072
73
74
75
76
77
78
79
80
81
82
83
84
85
86
Episode 6	Average Score: -0.005087
88
89
90
91
92
93
94
95
96
97
98
99
100
Episode 7	Average Score: -0.0050101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
Episode 8	Average Score: -0.0050116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
Episode 9	Average Score: -0.0050131
132
133
134
135
136
137
138
139
140
141
142
143
144
Episode 10	Average Score: -0.00

1271
1272
1273
1274
1275
1276
1277
Episode 85	Average Score: -0.00381278
1279
1280
1281
1282
1283
1284
1285
1286
1287
1288
1289
1290
1291
Episode 86	Average Score: -0.00381292
1293
1294
1295
1296
1297
1298
1299
1300
1301
1302
1303
1304
1305
Episode 87	Average Score: -0.00391306
1307
1308
1309
1310
1311
1312
1313
1314
1315
1316
1317
1318
1319
Episode 88	Average Score: -0.00391320
1321
1322
1323
1324
1325
1326
1327
1328
1329
1330
1331
1332
1333
1334
Episode 89	Average Score: -0.00391335
1336
1337
1338
1339
1340
1341
1342
1343
1344
1345
1346
1347
1348
Episode 90	Average Score: -0.00391349
1350
1351
1352
1353
1354
1355
1356
1357
1358
1359
1360
1361
1362
Episode 91	Average Score: -0.00391363
1364
1365
1366
1367
1368
1369
1370
1371
1372
1373
1374
1375
1376
Episode 92	Average Score: -0.00391377
1378
1379
1380
1381
1382
1383
1384
1385
1386
1387
1388
1389
1390
Episode 93	Average Score: -0.00391391
1392
1393
1394
1395
1396
1397
1398
1399
1400
1401
1402
1403
1404
1405
Episode 94	Average Score: -0

2391
2392
2393
2394
2395
2396
2397
2398
2399
Episode 164	Average Score: -0.00502400
2401
2402
2403
2404
2405
2406
2407
2408
2409
2410
2411
2412
2413
Episode 165	Average Score: -0.00502414
2415
2416
2417
2418
2419
2420
2421
2422
2423
2424
2425
2426
2427
Episode 166	Average Score: -0.00502428
2429
2430
2431
2432
2433
2434
2435
2436
2437
2438
2439
2440
2441
Episode 167	Average Score: -0.00502442
2443
2444
2445
2446
2447
2448
2449
2450
2451
2452
2453
2454
2455
Episode 168	Average Score: -0.00502456
2457
2458
2459
2460
2461
2462
2463
2464
2465
2466
2467
2468
2469
2470
Episode 169	Average Score: -0.00502471
2472
2473
2474
2475
2476
2477
2478
2479
2480
2481
2482
2483
2484
Episode 170	Average Score: -0.00502485
2486
2487
2488
2489
2490
2491
2492
2493
2494
2495
2496
2497
2498
Episode 171	Average Score: -0.00502499
2500
2501
2502
2503
Stop adding noise

Stop adding noise

2504
Stop adding noise

Stop adding noise

2505
Stop adding noise

Stop adding noise

2506
Stop adding noise

Stop adding noi

...

63891
Stop adding noise

Stop adding noise

63892
Stop adding noise

Stop adding noise

63893
Stop adding noise

Stop adding noise

63894
Stop adding noise

Stop adding noise

63895
Stop adding noise

Stop adding noise

63896
Stop adding noise

Stop adding noise

63897
Stop adding noise

Stop adding noise

63898
Stop adding noise

Stop adding noise

63899
Episode 3801	Average Score: 0.0115Stop adding noise

Stop adding noise

63900
Stop adding noise

Stop adding noise

63901
Stop adding noise

Stop adding noise

63902
Stop adding noise

Stop adding noise

63903
Stop adding noise

Stop adding noise

63904
Stop adding noise

Stop adding noise

63905
Stop adding noise

Stop adding noise

63906
Stop adding noise

Stop adding noise

63907
Stop adding noise

Stop adding noise

63908
Stop adding noise

Stop adding noise

63909
Stop adding noise

Stop adding noise

63910
Stop adding noise

Stop adding noise

63911
Stop adding noise

Stop adding noise

63912
Stop adding noise

Stop adding noise


Stop adding noise

64079
Stop adding noise

Stop adding noise

64080
Stop adding noise

Stop adding noise

64081
Stop adding noise

Stop adding noise

64082
Stop adding noise

Stop adding noise

64083
Stop adding noise

Stop adding noise

64084
Stop adding noise

Stop adding noise

64085
Stop adding noise

Stop adding noise

64086
Stop adding noise

Stop adding noise

64087
Stop adding noise

Stop adding noise

64088
Stop adding noise

Stop adding noise

64089
Stop adding noise

Stop adding noise

64090
Stop adding noise

Stop adding noise

64091
Stop adding noise

Stop adding noise

64092
Episode 3810	Average Score: 0.0120Stop adding noise

Stop adding noise

64093
Stop adding noise

Stop adding noise

64094
Stop adding noise

Stop adding noise

64095
Stop adding noise

Stop adding noise

64096
Stop adding noise

Stop adding noise

64097
Stop adding noise

Stop adding noise

64098
Stop adding noise

Stop adding noise

64099
Stop adding noise

Stop adding noise

64100
Stop adding nois

64261
Stop adding noise

Stop adding noise

64262
Stop adding noise

Stop adding noise

64263
Stop adding noise

Stop adding noise

64264
Stop adding noise

Stop adding noise

64265
Stop adding noise

Stop adding noise

64266
Stop adding noise

Stop adding noise

64267
Stop adding noise

Stop adding noise

64268
Stop adding noise

Stop adding noise

64269
Stop adding noise

Stop adding noise

64270
Stop adding noise

Stop adding noise

64271
Stop adding noise

Stop adding noise

64272
Stop adding noise

Stop adding noise

64273
Stop adding noise

Stop adding noise

64274
Stop adding noise

Stop adding noise

64275
Stop adding noise

Stop adding noise

64276
Stop adding noise

Stop adding noise

64277
Stop adding noise

Stop adding noise

64278
Stop adding noise

Stop adding noise

64279
Stop adding noise

Stop adding noise

64280
Stop adding noise

Stop adding noise

64281
Stop adding noise

Stop adding noise

64282
Stop adding noise

Stop adding noise

64283
Stop adding noise

Stop ad

64446
Stop adding noise

Stop adding noise

64447
Stop adding noise

Stop adding noise

64448
Stop adding noise

Stop adding noise

64449
Stop adding noise

Stop adding noise

64450
Stop adding noise

Stop adding noise

64451
Stop adding noise

Stop adding noise

64452
Stop adding noise

Stop adding noise

64453
Stop adding noise

Stop adding noise

64454
Stop adding noise

Stop adding noise

64455
Episode 3825	Average Score: 0.0130Stop adding noise

Stop adding noise

64456
Stop adding noise

Stop adding noise

64457
Stop adding noise

Stop adding noise

64458
Stop adding noise

Stop adding noise

64459
Stop adding noise

Stop adding noise

64460
Stop adding noise

Stop adding noise

64461
Stop adding noise

Stop adding noise

64462
Stop adding noise

Stop adding noise

64463
Stop adding noise

Stop adding noise

64464
Stop adding noise

Stop adding noise

64465
Stop adding noise

Stop adding noise

64466
Stop adding noise

Stop adding noise

64467
Stop adding noise

Stop adding noise

Stop adding noise

Stop adding noise

64631
Stop adding noise

Stop adding noise

64632
Stop adding noise

Stop adding noise

64633
Stop adding noise

Stop adding noise

64634
Stop adding noise

Stop adding noise

64635
Stop adding noise

Stop adding noise

64636
Stop adding noise

Stop adding noise

64637
Stop adding noise

Stop adding noise

64638
Stop adding noise

Stop adding noise

64639
Stop adding noise

Stop adding noise

64640
Stop adding noise

Stop adding noise

64641
Stop adding noise

Stop adding noise

64642
Stop adding noise

Stop adding noise

64643
Stop adding noise

Stop adding noise

64644
Stop adding noise

Stop adding noise

64645
Episode 3835	Average Score: 0.0140Stop adding noise

Stop adding noise

64646
Stop adding noise

Stop adding noise

64647
Stop adding noise

Stop adding noise

64648
Stop adding noise

Stop adding noise

64649
Stop adding noise

Stop adding noise

64650
Stop adding noise

Stop adding noise

64651
Stop adding noise

Stop adding noise

6465

In [ ]:
for i in range(1, 6):                                      # play game for 5 episodes
    env_info = env.reset(train_mode=False)[brain_name]     # reset the environment    
    states = env_info.vector_observations                  # get the current state (for each agent)
    scores = np.zeros(num_agents)                          # initialize the score (for each agent)
    t = 0
    while True:
        actions = agent.act(states,add_noise=False)        # select an action (for each agent)
        env_info = env.step(actions)[brain_name]           # send all actions to tne environment
        next_states = env_info.vector_observations         # get next state (for each agent)
        rewards = env_info.rewards                         # get reward (for each agent)
        dones = env_info.local_done                        # see if episode finished
        agent.step(states, actions, rewards, next_states, dones, t)
        scores += env_info.rewards                         # update the score (for each agent)
        states = next_states                               # roll over states to next time step
        t+=1
        if np.any(dones):                                  # exit loop if episode finished
            break
    print('Score (max over agents) from episode {}: {:.4f}'.format(i, np.max(scores)))